In [15]:
##conda install -c conda-forge vl-convert-python


In [16]:
import pandas as pd
import altair as alt

In [17]:
emissionsData = pd.read_csv('../data/CombinedCSV.csv')
emissionsData.head()

Country  Year  Population     GDP (USD)  Total Emissions  \
0  Afghanistan  1970    10752971  1.748887e+09        17.336192   
1  Afghanistan  1971    11015857  1.831109e+09        17.292793   
2  Afghanistan  1972    11286753  1.595555e+09        15.342251   
3  Afghanistan  1973    11575305  1.733333e+09        15.966060   
4  Afghanistan  1974    11869879  2.155555e+09        17.278443   

   CO2 Agriculture  CO2 Buildings  CO2 Fuel Exploitation  \
0         0.029229       0.795304               0.337834   
1         0.029229       0.795304               0.346137   
2         0.029229       0.606946               0.417038   
3         0.029229       0.740247               0.254414   
4         0.039967       0.972635               0.417052   

   CO2 Industrial Combustion  CO2 Power Industry  ...  CH4 Waste   \
0                   0.101666            0.057193  ...    1.520051   
1                   0.101666            0.057193  ...    1.569643   
2                   0.094763            0.117373  ...    1.611488   
3                   0.096220            0.175702  ...    1.656953   
4                   0.105739            0.207734  ...    1.700537   

   F-Gases Processes  N2O Agriculture  N2O Buildings  N2O Fuel Exploitation  \
0                0.0         2.437757       0.003569               0.001825   
1                0.0         2.400889       0.003631               0.001856   
2                0.0         1.874531       0.003605               0.002148   
3                0.0         2.056200       0.003812               0.001539   
4                0.0         2.249199       0.004235               0.002161   

   N2O Industrial Combustion  N2O Power Industry  N2O Processes  \
0                   0.000376            0.000101       0.008604   
1                   0.000376            0.000101       0.008644   
2                   0.000341            0.000203       0.009167   
3                   0.000350            0.000291       0.009418   
4                   0.000382            0.000347       0.010483   

   N2O Transport  N2O Waste  
0       0.001963   0.057916  
1       0.001970   0.060965  
2       0.002270   0.064013  
3       0.002160   0.067061  
4       0.002267   0.070109  

[5 rows x 30 columns]

In [18]:
selection = alt.selection_point(fields = ['Country'], value = 'United States')

color = alt.condition(
    selection,
    alt.Color('Country:N', scale=alt.Scale(scheme='category20'), legend = None),
    alt.value('lightgrey')
)

chart = alt.Chart(emissionsData, width=800, height=780).mark_line().encode(
    x = 'Year:N',
    y = alt.Y('Total Emissions:Q', scale=alt.Scale(type='log'), axis=alt.Axis(title='Total Emissions (mt)')),
    color = color
).properties(
    title = 'Total Green House Gas Emissions per Country (1970 - 2022)'
)

legend = alt.Chart(emissionsData).mark_circle().encode(
    alt.Y('Country:N').axis(orient = 'right'),
    color = color
).add_params(
    selection
)

# Display the chart
(chart | legend).configure_axis(
    grid=False
).configure_view(
    stroke=None
).display()

#(chart | legend).save('chart.html')


alt.HConcatChart(...)

In [19]:

emissions_bySector = pd.read_csv("../data/emissions_bySector.csv", encoding ='latin1')

selectedCountries = ['Afghanistan', 'Albania', 'Aruba', 'Australia', 'Bahamas', 'Brazil', 'Canada', 'Cayman Islands', 'Chile', 'China', 'Cuba', 'Egypt', 
                     'Fiji', 'Germany', 'Greece', 'Greenland', 'Iceland', 'India', 'Indonesia', 'Iran', 'Iraq', 'Jamaica', 'Japan', 'Liberia', 
                     'Luxembourg', 'Mexico', 'Netherlands', 'Pakistan', 'Qatar', 'Russia', 'Saudi Arabia', 'Singapore', 'South Africa', 'South Korea', 
                     'Sudan and South Sudan', 'Sweden', 'Türkiye', 'United Arab Emirates', 'Ukraine', 'United Kingdom', 'United States', 'Vietnam']

selected_lesser_countries = ['Afghanistan', 'Albania', 'Aruba', 'Bahamas', 'Cayman Islands', 'Chile', 'Cuba', 'Egypt', 
                     'Fiji', 'Greece', 'Greenland', 'Iceland', 'Jamaica', 'Liberia', 
                     'Luxembourg', 'Mexico', 'Netherlands', 'Qatar', 'Singapore', 
                     'Sudan and South Sudan', 'Sweden', 'United Arab Emirates', 'Ukraine', 'Vietnam']


filteredEmissions = emissions_bySector[emissions_bySector['Country'].isin(selectedCountries)]

country_dropdown = alt.binding_select(options = selected_lesser_countries, name = 'Country 1 ')
country_selection = alt.selection_point(fields = ['Country'], bind = country_dropdown, value = 'Afghanistan')

country_dropdown2 = alt.binding_select(options = selected_lesser_countries, name = 'Country 2 ')
country_selection2 = alt.selection_point(fields = ['Country'], bind = country_dropdown2, value = 'Albania')


max_value = filteredEmissions['2022'].max()

chart_comparison = alt.Chart(filteredEmissions, title=alt.Title(
       "Comparison of Sector Specific Emissions (2022)",
       subtitle="Lowest Producing Countries")).transform_filter(
    country_selection
).mark_bar().encode(
    alt.Tooltip(['Substance:N', '2022:Q']),
    x = alt.X('2022:Q', title = '2022 Emissions (mt)', scale=alt.Scale(domain=[0, 150])),
    y = alt.Y('Sector:N'),
    color = alt.Color('Substance:N', scale = alt.Scale(scheme = 'set1')),
    column = alt.Column('Country:N', title = None)
).add_params(
    country_selection
).properties(
    width = 250,
    height = 400
)

chart_us = alt.Chart(filteredEmissions).transform_filter(
    ##alt.datum.Country == 'United States'
    country_selection2
).mark_bar().encode(
    alt.Tooltip(['Substance:N', '2022:Q']),
    x = alt.X('2022:Q', title = '2022 Emissions (mt)', scale=alt.Scale(domain=[0, 150])),
    y = alt.Y('Sector:N', title = None),
    color = alt.Color('Substance:N', scale = alt.Scale(scheme = 'set1')),
    column = alt.Column('Country:N', title = None)
).add_params(
    country_selection2
).properties(
    width = 250,
    height = 400
)

(chart_comparison | chart_us).display()

#(chart_comparison | chart_us).save('chart_comp.html')

alt.HConcatChart(...)

In [20]:

emissions_bySector = pd.read_csv("../data/emissions_bySector.csv", encoding ='latin1')

selectedCountries = ['Afghanistan', 'Albania', 'Aruba', 'Australia', 'Bahamas', 'Brazil', 'Canada', 'Cayman Islands', 'Chile', 'China', 'Cuba', 'Egypt', 
                     'Fiji', 'Germany', 'Greece', 'Greenland', 'Iceland', 'India', 'Indonesia', 'Iran', 'Iraq', 'Jamaica', 'Japan', 'Liberia', 
                     'Luxembourg', 'Mexico', 'Netherlands', 'Pakistan', 'Qatar', 'Russia', 'Saudi Arabia', 'Singapore', 'South Africa', 'South Korea', 
                     'Sudan and South Sudan', 'Sweden', 'Türkiye', 'United Arab Emirates', 'Ukraine', 'United Kingdom', 'United States', 'Vietnam']

selected_greater_countries = ['China', 'United States', 'India', 'Russia', 'Brazil', 'Indonesia', 'Japan', 'Iran', 'Mexico', 'Saudi Arabia', 'Germany', 'Canada', 'South Korea', 'Türkiye', 'Australia', 'Pakistan', 'Iraq', 'South Africa']


filteredEmissions = emissions_bySector[emissions_bySector['Country'].isin(selectedCountries)]

country_dropdown3 = alt.binding_select(options = selected_greater_countries, name = 'Country 1 ')
country_selection3 = alt.selection_point(fields = ['Country'], bind = country_dropdown3, value = 'China')

country_dropdown4 = alt.binding_select(options = selected_greater_countries, name = 'Country 2 ')
country_selection4 = alt.selection_point(fields = ['Country'], bind = country_dropdown4, value = 'United States')


max_value = filteredEmissions['2022'].max()

chart_comparison = alt.Chart(filteredEmissions, title=alt.Title(
       "Comparison of Sector Specific Emissions (2022)",
       subtitle="Highest Producing Countries"
   )).transform_filter(
    country_selection3
).mark_bar().encode(
    alt.Tooltip(['Substance:N', '2022:Q']),
    x = alt.X('2022:Q', title = '2022 Emissions (mt)', scale=alt.Scale(domain=[0, max_value])),
    y = alt.Y('Sector:N'),
    color = alt.Color('Substance:N', scale = alt.Scale(scheme = 'set1')),
    column = alt.Column('Country:N', title = None)
).add_params(
    country_selection3
).properties(
    width = 250,
    height = 400
)

chart_us = alt.Chart(filteredEmissions).transform_filter(
    ##alt.datum.Country == 'United States'
    country_selection4
).mark_bar().encode(
    alt.Tooltip(['Substance:N', '2022:Q']),
    x = alt.X('2022:Q', title = '2022 Emissions (mt)', scale=alt.Scale(domain=[0, max_value])),
    y = alt.Y('Sector:N', title = None),
    color = alt.Color('Substance:N', scale = alt.Scale(scheme = 'set1')),
    column = alt.Column('Country:N', title = None)
).add_params(
    country_selection4
).properties(
    width = 250,
    height = 400
)

(chart_comparison | chart_us).display()

#(chart_comparison | chart_us).save('chart_comp2.html')

alt.HConcatChart(...)

In [21]:
country_by_region = pd.read_csv("../data/Countries by continents.csv")

emissions_region = pd.merge(emissionsData, country_by_region, left_on = 'Country', right_on = 'Country', how = 'outer')

emissions_region.head()

Country    Year  Population     GDP (USD)  Total Emissions  \
0  Afghanistan  1970.0  10752971.0  1.748887e+09        17.336192   
1  Afghanistan  1971.0  11015857.0  1.831109e+09        17.292793   
2  Afghanistan  1972.0  11286753.0  1.595555e+09        15.342251   
3  Afghanistan  1973.0  11575305.0  1.733333e+09        15.966060   
4  Afghanistan  1974.0  11869879.0  2.155555e+09        17.278443   

   CO2 Agriculture  CO2 Buildings  CO2 Fuel Exploitation  \
0         0.029229       0.795304               0.337834   
1         0.029229       0.795304               0.346137   
2         0.029229       0.606946               0.417038   
3         0.029229       0.740247               0.254414   
4         0.039967       0.972635               0.417052   

   CO2 Industrial Combustion  CO2 Power Industry  ...  F-Gases Processes  \
0                   0.101666            0.057193  ...                0.0   
1                   0.101666            0.057193  ...                0.0   
2                   0.094763            0.117373  ...                0.0   
3                   0.096220            0.175702  ...                0.0   
4                   0.105739            0.207734  ...                0.0   

   N2O Agriculture  N2O Buildings  N2O Fuel Exploitation  \
0         2.437757       0.003569               0.001825   
1         2.400889       0.003631               0.001856   
2         1.874531       0.003605               0.002148   
3         2.056200       0.003812               0.001539   
4         2.249199       0.004235               0.002161   

   N2O Industrial Combustion  N2O Power Industry  N2O Processes  \
0                   0.000376            0.000101       0.008604   
1                   0.000376            0.000101       0.008644   
2                   0.000341            0.000203       0.009167   
3                   0.000350            0.000291       0.009418   
4                   0.000382            0.000347       0.010483   

   N2O Transport  N2O Waste  Continent  
0       0.001963   0.057916       Asia  
1       0.001970   0.060965       Asia  
2       0.002270   0.064013       Asia  
3       0.002160   0.067061       Asia  
4       0.002267   0.070109       Asia  

[5 rows x 31 columns]

In [22]:
emissions_continent_year_agg = emissions_region.groupby(['Continent', 'Year']).agg({
    'GDP (USD)': 'sum',
    'Total Emissions': 'sum'
}).reset_index()

chart_scatter = alt.Chart(emissions_continent_year_agg).mark_circle().encode(
    x=alt.X('GDP (USD):Q', title='Total GDP by Year (USD)').scale(type='log'),
    y=alt.Y('Total Emissions:Q', title='Total Emissions by Year (mt)').scale(type='log'),
    color=alt.Color('Continent:N', scale=alt.Scale(scheme='category10')),
    size=alt.Size(value=70),
    opacity = alt.Opacity(value = 0.5)
).properties(
    width=500,
    height=300,
    title='Total Emissions vs Total GDP by Year and Continent'
)


# Display the chart
(chart_scatter).display()

#(chart_scatter).save('chart_scatter.html')


alt.Chart(...)

In [23]:
emissionsData['Emissions per Capita'] = emissionsData['Total Emissions'] / emissionsData['Population']
max_emit_capita = emissionsData['Emissions per Capita'].max()
max_emit_total = emissionsData['Total Emissions'].max()

selectedCountries_ = ['Afghanistan', 'Albania', 'Aruba', 'Australia', 'Bahamas', 'Brazil', 'Canada', 'Cayman Islands', 'Chile', 'China', 'Cuba', 'Egypt', 
                     'Fiji', 'Germany', 'Greece', 'Greenland', 'Iceland', 'India', 'Indonesia', 'Iran', 'Iraq', 'Jamaica', 'Japan', 'Liberia', 
                     'Mexico', 'Netherlands', 'Pakistan', 'Russia', 'Saudi Arabia', 'Singapore', 'South Africa', 'South Korea', 
                     'Sudan and South Sudan', 'Sweden', 'Türkiye', 'Ukraine', 'United Kingdom', 'United States', 'Vietnam']

chart_width = 700
chart_height = 290


country_dropdown5 = alt.binding_select(options = selectedCountries_, name = 'Country 1 ')
country_selection5 = alt.selection_point(fields=['Country'], bind=country_dropdown5, value='United States')

country_dropdown6 = alt.binding_select(options = selectedCountries_, name = 'Country 2 ')
country_selection6 = alt.selection_point(fields=['Country'], bind=country_dropdown6, value ='China')

# Define the chart
chart = alt.Chart(emissionsData, width = chart_width, height = chart_height).transform_filter(
    country_selection5 | country_selection6
).mark_line(opacity=0.2).encode(
    alt.Tooltip(['Country:N', 'Emissions per Capita:Q', 'Total Emissions:Q', 'Population:Q', 'Year:N']),
    x=alt.X('Year:N'),
    ##y=alt.Y('Emissions per Capita:Q', scale=alt.Scale(type='linear')),  # Set y-axis scale to linear
    y=alt.Y('Emissions per Capita:Q', scale=alt.Scale(domain=[0, 0.00003]), title = 'Emissions per Capita (mt)'),  # Set y-axis scale to linear
    color=alt.Color('Country:N', legend=alt.Legend(title="Country", orient='bottom'), scale = alt.Scale(scheme = 'set1')),
).add_params(
    country_selection5, country_selection6
).properties(
    width = chart_width,
    height = chart_height
)

dots = chart.mark_point().encode(
    x='Year:N',
    y=alt.Y('Emissions per Capita:Q', scale=alt.Scale(domain=[0, 0.00003])),
    color=alt.Color('Country:N', legend=alt.Legend(title="Country", orient='bottom'), scale = alt.Scale(scheme = 'set1')),
    size = alt.Size('Population:Q', legend=alt.Legend(title="Population", orient='bottom'))
)


total_emissions_chart = alt.Chart(emissionsData).transform_filter(
    country_selection5 | country_selection6
).mark_line(strokeDash=[3,3]).encode(
    x='Year:N',
    y=alt.Y('Total Emissions:Q', scale=alt.Scale(domain=[0, max_emit_total]), title = 'Total Emissions (mt)'),
    color=alt.Color('Country:N', legend=alt.Legend(title="Country", orient = 'bottom'), scale = alt.Scale(scheme = 'set1'))
).add_params(
    country_selection5, country_selection6
).properties(
    width = chart_width,
    height = chart_height
)

combined = ((chart + dots) & (total_emissions_chart)).properties(title = 'Country Comparison of Emissions per Capita and Total Emissions (1970 - 2022)')

combined.add_params(
    country_selection5, country_selection6
).display()

#combined.save('chart_capita.html')


alt.VConcatChart(...)